In [1]:
import pandas as pd
from IPython.display import clear_output, Markdown, Math
import ipywidgets as widgets
import os
import glob
import json
import numpy as np
import itertools
import sklearn.utils as sku
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer, HashingVectorizer
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MultiLabelBinarizer

In [2]:
import sys
sys.path.append("..")

from Tools.Emoji_Distance import sentiment_vector_to_emoji
from Tools.Emoji_Distance import emoji_to_sentiment_vector

def emoji2sent(emoji_arr):
    return np.array([emoji_to_sentiment_vector(e) for e in emoji_arr])

def sent2emoji(sent_arr):
    return [sentiment_vector_to_emoji(s) for s in sent_arr]

In [3]:
SINGLE_LABEL = True

# simple twitter approach
*for learning emoji usage by single (in the meaning of unconnected) twitter messages*

## loading train data

In [4]:
data_root_folder = "./data_en/" # i created a symlink here

* get all json files in `data_root_folder`

In [5]:
json_files = sorted(glob.glob(data_root_folder + "/*.json"))

----

* so far, only load the first file

In [6]:
twitter_data = pd.read_json(json_files[0], encoding="utf-8")
twitter_data

EMOJI  \
0                           [🔥, 👏]   
1                              [🤦]   
2                              [😄]   
3                              [📷]   
4                           [😩, 😩]   
5                           [😭, 💓]   
6                              [😂]   
7                              [💯]   
8                              [🙄]   
9                        [😟, 😥, 😢]   
10                             [🌻]   
11                       [🍁, 🌺, 🍂]   
12                             [🍃]   
13                          [💭, 🤦]   
14                          [😍, 😘]   
15                             [😜]   
16                          [😂, 🔥]   
17                             [💕]   
18                             [😉]   
19                             [👅]   
20                          [👌, 🙂]   
21                          [🤗, 📺]   
22                             [💯]   
23                       [👅, 💦, 🍑]   
24                             [💔]   
25                       [🤐, 🤐, 🤐]   
26                             [😴]   
27                             [😂]   
28                          [😂, 🙄]   
29              [🎉, 🎂, 🎈, 🎊, 🎁, 💜]   
...                            ...   
68703                          [😕]   
68704                       [😂, 😩]   
68705                          [😂]   
68706                          [💖]   
68707                 [🌆, 👉, 🚖, 📞]   
68708                          [😁]   
68709                          [😋]   
68710                    [👌, 🎃, 😘]   
68711                          [👍]   
68712                          [😭]   
68713                          [😂]   
68714                    [😭, 😭, 💘]   
68715                       [😫, ✋]   
68716                       [😂, 🙁]   
68717                          [😭]   
68718                       [😢, 💔]   
68719                          [🙃]   
68720              [😂, 😂, 😂, 😂, 😂]   
68721                    [👌, 👊, 🙌]   
68722                          [😴]   
68723                 [😂, 😂, 😂, 😂]   
68724                          [😀]   
68725                          [😎]   
68726                          [✨]   
68727                          [🤷]   
68728                          [😘]   
68729                          [😂]   
68730                          [🙏]   
68731                          [💁]   
68732  [🍃, 🌻, 🌻, 🍃, 🍃, 💐, 💐, 🍃, 🙋]   

                                              HASHTAGS  \
0                                                   []   
1                                                   []   
2                                                   []   
3                                                   []   
4                                                   []   
5                                                   []   
6                                                   []   
7                                                   []   
8                                                   []   
9                                                   []   
10                                                  []   
11                                                  []   
12         [#mortdale, #partofthefamily, #gorgeousboy]   
13                                                  []   
14                                     [#7YearsOfKMH2]   
15                                                  []   
16                                                  []   
17                                                  []   
18                                                  []   
19                                 [#footfetishnation]   
20                                                  []   
21                                                  []   
22                                                  []   
23                                                  []   
24                                                  []   
25                                                  []   
26                                                  []   
27                                              

* extracting emojis and text

In [7]:
emojis = twitter_data['EMOJI']
plain_text = twitter_data['text']

* make our plain text more "plain":
    * removing the keyword `<EMOJI>` (just for the beginning)
    * removing remaining useless emojis, like skin modifier etc.

In [8]:
# defining blacklist for modifier emojis:
emoji_blacklist = set([
    chr(0x1F3FB),
    chr(0x1F3FC),
    chr(0x1F3FD),
    chr(0x1F3FE),
    chr(0x1F3FF),
    chr(0x2642),
    chr(0x2640)
])

In [9]:
# filtering them and the EMOJI keyword out:
plain_text = plain_text.str.replace("(<EMOJI>|<USER>|<HASHTAG>)","").str.replace("[" + "".join(list(emoji_blacklist)) + "]","")

* defining different criterias for choosing a single emoji (currently `latest` is used)

In [10]:
def latest(lst):
    return lst[-1] if len(lst) > 0 else 'X' 
def most_common(lst):
    # trying to find the most common used emoji in the given lst
    return max(set(lst), key=lst.count) if len(lst) > 0 else "X" # setting label to 'X' if there is an empty emoji list

* convert all emojis to a sentiment vector

In [11]:
labels = emoji2sent([latest(e) for e in emojis])


In [12]:
len(labels)

68733

In [13]:
wrong_labels = np.isnan(np.linalg.norm(labels, axis=1))

* remove all data we have no label for

In [14]:
labels = labels[np.invert(wrong_labels)]
plain_text = plain_text[np.invert(wrong_labels)]
emojis = emojis[np.invert(wrong_labels)]

In [15]:
print(len(labels), len(emojis), len(plain_text))

33368 33368 33368


* generate weights:

In [16]:
# at first count over our table
emoji_count = {}


for e_list in emojis:
    for e in set(e_list):
        if e not in emoji_count:
            emoji_count[e] = 0
        emoji_count[e] += 1

emoji_count
emoji_sum = sum([emoji_count[e] for e in emoji_count])

emoji_weights = {}
for e in emoji_count:
    # tfidf for emojis
    emoji_weights[e] = np.log((emoji_sum / emoji_count[e]))

weights_sum= sum([emoji_weights[x] for x in emoji_weights])
    
# normalize:
for e in emoji_weights:
    emoji_weights[e] = emoji_weights[e] / weights_sum

emoji_weights['X'] = 0  # dummy values
emoji_count['X'] = 0

* most used emojis in Dataset

In [17]:
import operator

In [18]:
sorted_emoji_count = list(reversed(sorted(emoji_count.items(), key=operator.itemgetter(1))))
display(sorted_emoji_count[:5])

top_emojis = [x[0] for x in sorted_emoji_count[:5]]
display(top_emojis)

[('😂', 10182), ('😭', 3893), ('😍', 2866), ('😩', 1647), ('😊', 1450)]

['😂', '😭', '😍', '😩', '😊']

* only learn the most used ones:

In [19]:
in_top = [sentiment_vector_to_emoji(x) in top_emojis for x in labels]
labels = labels[in_top]
plain_text = plain_text[in_top]
emojis = emojis[in_top]
print(len(labels), len(emojis), len(plain_text))

17815 17815 17815


* generating train and test set:

In [20]:
X1, Xt1, y1, yt1 = train_test_split(plain_text, labels, test_size=0.1, random_state=4222)

In [21]:
#y1_weights = np.array([(sum([emoji_weights[e] for e in e_list]) / len(e_list)) if len(e_list) > 0 else 0 for e_list in sent2emoji(y1)])

In [22]:
vectorizer = TfidfVectorizer(stop_words='english')
vec_train = vectorizer.fit_transform(X1)
vec_test = vectorizer.transform(Xt1)

* train. this can take a very long time...

In [23]:
from sklearn.neural_network import MLPClassifier as MLP
from sklearn.multiclass import OneVsRestClassifier as OVRC
from sklearn.tree import DecisionTreeClassifier as DTC

from keras.models import Sequential
from keras.layers import Dense

Using TensorFlow backend.


In [24]:
def train(max_size = 10000, layers=[(1024, 'relu'),(y1[0].shape[0],'softmax')], random_state=4222, ovrc=False, n_iter=5):
    
    model = Sequential()
    
    # build mlp layers:
    keras_layers = []
    first_layer = True
    for layer in layers:
        if first_layer:
            model.add(Dense(units=layer[0], activation=layer[1], input_dim=vectorizer.transform([" "])[0]._shape[1]))
            first_layer = False
        else:
            model.add(Dense(units=layer[0], activation=layer[1]))
    
    #mlp = MLPClassifier(layers=sknn_layers, random_state=random_state, verbose=True, n_iter=n_iter, batch_size=100)
    
    model.compile(loss='mean_squared_error',
              optimizer='adam')
    
    clf = OVRC(model) if ovrc else model

    clf.fit(vec_train[:max_size].A, y1[:max_size], validation_split=0.2, epochs=n_iter)#, sample_weight=y1_weights[:max_size])
    
    return clf

In [26]:
clf = train(max_size=10000,layers=[(10000, 'relu'),(y1[0].shape[0],'softmax')], n_iter=1)

Train on 8000 samples, validate on 2000 samples
Epoch 1/1
8000/8000 [==============================] - 311s 39ms/step - loss: 0.0145 - val_loss: 0.0132


* make a prediction and store it in a csv file:

In [27]:
pred = clf.predict(vectorizer.transform(Xt1))

In [28]:
print(np.linalg.norm(np.var(pred, axis=0)))
print(np.linalg.norm(np.var(labels)))


0.005192853
0.02568319204819897


In [29]:
# build a dataframe to visualize test results:
testlist = pd.DataFrame({'text': Xt1, 
                         'teacher': sent2emoji(yt1),
                         'teacher_sentiment': yt1.tolist(),
                         'predict': sent2emoji(pred),
                         'predicted_sentiment': pred.tolist()})

In [30]:
display(testlist)


text teacher  \
35056              I LOVE YOU OMG HOW DID I GET SO LUCKY       😍   
6745   Lol Palesa Blossom Mission Leomaure this guy i...       😂   
19721  I wish I can take a video of how I am laughing...       😂   
37748  The Adulting Awards on the commitment session ...       😂   
43315                             Good English Valencia        😂   
35986                              Yeahhhh righhhhttttt        😂   
21986                            Anything for my baby.         😭   
50154                    HBD PRETTY GIRL I LOVE YOU SM         😍   
49516                              Cba for these boots         😭   
16799                          That rose gold one! OMG         😍   
50674   just ended I can't explain feelings  a great ...       😭   
16560  //I'm a male account and I can't even ask some...       😍   
33071  A Lebanese Christian (I dont even know him) se...       😂   
52543                     I've seen this too many times        😂   
18733                                       HahahYESSSSS       😂   
12353  Sure.. That's so stupid ,. They just have to b...       😩   
49480                                     Ok makes sense       😂   
32767  They call you bitches and act like they moved ...       😂   
32938  On Christ himself that glossy lip, smooth brow...       😭   
46800                          Let her enjoy wena mahn         😂   
68700                            person that scares me         😂   
34936                Dodson put him on his back pockets        😂   
63804  I can’t wait to put a countdown in my name for...       😭   
13670                                     My chest hurt        😩   
36792  Ready to be back in Chicago for some good eats...       😂   
54093                                  I didn't see this       😂   
21937                   I wonder have I met my wife yet        😂   
45980                               why deep sorrow man        😂   
38860                          Haha I had it on earlier        😂   
33399                                        this gif!!!       😂   
...                                                  ...     ...   
13242   Studying abroad in Italy for 3 weeks  it won'...       😭   
25032           I am weird too soo what's the problem ?        😂   
44255                            Cuz he knows you strong       😂   
26815  This is what having 3 dogs is like! It takes A...       😂   
47744                                  LMFAO!!!!!!!!!!         😂   
19837                                            Monet.        😍   
17457  I don’t know why, but I kinda feel bad for the...       😂   
52462                              Haha was howling man        😂   
43377                                     Dyed my hair         😊   
25833   are you @ me  aha I love thanksgiving, but Ch...       😂   
67536    Who said there ain't no baseball in November          😂   
36246  trying to be the bigger person in this situati...       😭   
67247  So yeah I went to Enternal Gardens and heard B...       😂   
13370    São Paulo deserves a shout instead of that r...       😂   
65897   He is awesome ... remember his joke about 'pu...       😂   
59631         Yung feeling na last round 1v5 ace clutch        😂   
1643   I remember watching family guy til i got sleep...       😂   
16331                       Go ahead stalk my page away        😂   
3328    man you going bless the nature lmao trees don...       😂   
64995       Happy Birthday.  drinks in me this weekend.        😂   
7457                               I can't read English.       😭   
13454           I just surprised myself with that LMFAO        😂   
68032                                           Thisss         😍   
67183  No one understands how much I love ted I just ...       😩   
45526   Sry mt bol sis online a jaya kr  haan achi lg...       😂   
28803  Christian Organisations are lying as well, rig...       😂   
11554                                     I’m Dead Asf         😭   
68530                                   

In [31]:
testlist.to_csv('test.csv')

* a simple output widget for testing:

In [32]:
out = widgets.Output()

t = widgets.Text()
b = widgets.Button(
    description='get smiley',
    disabled=False,
    button_style='', # 'success', 'info', 'warning', 'danger' or ''
    tooltip='Click me',
    icon='check'
)



def handle_submit(sender):
    with out:
        clear_output()
    with out:
        pred = clf.predict(vectorizer.transform([t.value]))
        
        display(Markdown("# " + str(sent2emoji(pred))))

b.on_click(handle_submit)
    
display(t)
display(widgets.VBox([b, out]))  

Text(value='')

In [ ]:
import numpy as np

y_trans = mlb.inverse_transform(yt1)
pred_trans = mlb.inverse_transform(yt1)

# evaluate accuracy
pos = 0
neg = 0
all = 0
for entry in range(len(y_trans)):
    if len(np.intersect1d(y_trans[entry], pred_trans[entry])) > 0:
        pos += 1
    else:
        neg += 1
    all += 1
print(pos/all)
print(neg)